In [ ]:
import os, sys, shutil
from tqdm import tqdm
import numpy as np
import pandas as pd
import matplotlib as plt
from PIL import Image
from matplotlib.lines import Line2D
import matplotlib as mpl
import math
import matplotlib.image as mpimg
import random
# os.chdir("..")

In [110]:
#Experiment column key:
# 1: Experiment 1, mindeye vs second sight
# 2: Experiment 2, second sight two way identification
# 3: Experiment 3, mental imagery two way identification
df_exp = pd.DataFrame(columns=["experiment", "stim1", "stim2", "stim3", "sample", "subject", "target_on_left", "iter_count", "is_low", "method", "catch_trial", "rep", "mode", "trial_rep"])
i=0
random_count = 0
for subj in [1,2,5,7]: #1,2,5,7
    for sample in tqdm(range(982)):
        #count how many iterations the sample searched for
        iter_files = os.listdir(f"../output/mindeye_extension_v6/subject{subj}/{sample}/")
        iter_count = sum(1 for file in iter_files if "iter_" in file and file.endswith(".png"))
        
        #Experiment 1, mindeye vs second sight
        order = random.randrange(2)
        sample_names = [f"{sample}_subject{subj}_mindeye", f"{sample}_subject{subj}_secondsight"]
        
        left_sample = sample_names.pop(order)
        right_sample = sample_names.pop()
        gt_sample = f"{sample}_ground_truth"
        df_exp.loc[i] = {"experiment" : 1, "stim1" : gt_sample, "stim2" : left_sample, "stim3" : right_sample, "sample" : sample, "subject" : subj, 
                         "target_on_left" : order == 1, "iter_count" : iter_count, "is_low" : False, "method" : None, "catch_trial" : None, "rep" : 0, "mode" : "nsd_vision", "trial_rep" : 0}
        i+=1
        
        #Experiment 2, second sight two way identification
        order = random.randrange(2)
        shuffled_idx = [i for i in range(982)]
        random.shuffle(shuffled_idx)
        random_sample = shuffled_idx[sample]
        sample_names = [f"{random_sample}_subject{subj}_secondsight", f"{sample}_subject{subj}_secondsight"]
        
        left_sample = sample_names.pop(order)
        right_sample = sample_names.pop()
        gt_sample = f"{sample}_ground_truth"
        df_exp.loc[i] = {"experiment" : 2, "stim1" : gt_sample, "stim2" : left_sample, "stim3" : right_sample, "sample" : sample, "subject" : subj, 
                         "target_on_left" : order == 1, "iter_count" : iter_count, "is_low" : False, "method" : None, "catch_trial" : None, "rep" : 0, "mode" : "nsd_vision", "trial_rep" : 0}
        i+=1
    print(i)
    
    #Experiment 3, mental imagery two way identification
    random_count = {"mindeye" : 0, "braindiffuser" : 0, "tagaki" : 0, "secondsight" : 0}
    random_low_count = {"mindeye" : 0, "braindiffuser" : 0, "tagaki" : 0, "secondsight" : 0}
    for mode in ["vision", "imagery"]:
        for sample in range(12):
            gt_sample = f"mi_{sample}_ground_truth"
            for method in ["mindeye", "braindiffuser", "tagaki", "secondsight"]: 
                for rep in range(5):
                    for trial_rep in range(4):
                        order = random.randrange(2)
                        if method in ["mindeye", "secondsight"]:
                            shuffled_idx = [i for i in range(982)]
                            random.shuffle(shuffled_idx)
                            random_sample = shuffled_idx[sample]
                            sample_names = [f"{random_sample}_subject{subj}_{method}", f"mi_{sample}_subject{subj}_{method}_{mode}_{rep}"]
                        else:
                            sample_names = [f"{random_count[method]}_subject{subj}_{method}_random", f"mi_{sample}_subject{subj}_{method}_{mode}_{rep}"]
                            random_count[method] +=1
                        
                        left_sample = sample_names.pop(order)
                        right_sample = sample_names.pop()
                        #count how many iterations the sample searched for
                        if method == "secondsight":
                            iter_files = os.listdir(f"../output/ss_mi_{mode}/subject{subj}/{sample}/")
                            iter_count = sum(1 for file in iter_files if "iter_" in file and file.endswith(".png"))
                        else:
                            iter_count=None
                        
                        df_exp.loc[i] = {"experiment" : 3, "stim1" : gt_sample, "stim2" : left_sample, "stim3" : right_sample, "sample" : sample, "subject" : subj, 
                                        "target_on_left" : order == 1, "iter_count" : iter_count, "is_low" : False, "method" : method, "catch_trial" : None, "rep" : rep, "mode" : mode, "trial_rep" : trial_rep}
                        i+=1
                if method != "secondsight":
                    order = random.randrange(2)
                    sample_names = [f"{random_low_count[method]}_subject{subj}_{method}_low_random", f"mi_{sample}_subject{subj}_{method}_{mode}_low"]
                    random_low_count[method] +=1
                    left_sample = sample_names.pop(order)
                    right_sample = sample_names.pop()
                    df_exp.loc[i] = {"experiment" : 3, "stim1" : gt_sample, "stim2" : left_sample, "stim3" : right_sample, "sample" : sample, "subject" : subj, 
                                    "target_on_left" : order == 1, "iter_count" : None, "is_low" : True, "method" : method, "catch_trial" : None, "rep" : rep, "mode" : mode, "trial_rep" : 0}
                    i+=1                 
    print(i)
print(df_exp)
df_exp = df_exp.sample(frac=1)
print(df_exp)

  0%|          | 0/982 [00:00<?, ?it/s]

100%|██████████| 982/982 [00:09<00:00, 107.75it/s]


1964
3956


100%|██████████| 982/982 [00:15<00:00, 63.70it/s]


5920
7912


 12%|█▏        | 119/982 [00:02<00:18, 47.92it/s]


KeyboardInterrupt: 

In [ ]:
# Check if all images are present in final stimuli folder
count_not_found = 0
stim_path = "/home/naxos2-raid25/kneel027/home/kneel027/Second-Sight/experiments/final_stimuli/"
stim_path2 = "/home/naxos2-raid25/kneel027/home/kneel027/Second-Sight/experiments/new_random_stimuli/"
for index, row in df_exp.iterrows():
    if not (os.path.exists(f"{stim_path}{row['stim1']}.png") or os.path.exists(f"{stim_path2}{row['stim1']}.png")):
        print(f"{row['stim1']}.png")
        count_not_found += 1
    if not (os.path.exists(f"{stim_path}{row['stim2']}.png") or os.path.exists(f"{stim_path2}{row['stim2']}.png")):
        print(f"{row['stim2']}.png")
        count_not_found += 1
    if not (os.path.exists(f"{stim_path}{row['stim3']}.png") or os.path.exists(f"{stim_path2}{row['stim3']}.png")):
        print(f"{row['stim3']}.png")
        count_not_found += 1
print(count_not_found)

0


In [ ]:
#Add participant ID column
pIDs = []
for i in range(len(df_exp)):
    pIDs.append(i // 105)
df_exp.insert(0, "pID", pIDs)
print(len(df_exp[(df_exp['pID'] == 0)]))
#Add catch trials within each pID section
for pID in range(max(pIDs)):
    df_pid = df_exp[(df_exp['experiment'] == 2) & (df_exp['pID'] == pID)]
    
    # Ground truth catch trials
    gt_catch_trials = df_pid.sample(n=5)
    gt_catch_trials['catch_trial'] = "ground_truth"
    for index, row in gt_catch_trials.iterrows():
        
        order = random.randrange(2)
        ground_truth = row['stim1']
        stims = [row['stim2'], ground_truth]
        
        gt_catch_trials.at[index, 'stim2'] = stims.pop(order)
        gt_catch_trials.at[index, 'stim3'] = stims.pop()
        # Target on left here means the ground truth repeat is on the left
        gt_catch_trials.at[index, 'target_on_left'] = (order == 1)
        
    # repeated trial catch trials
    repeat_catch_trials_rep1 = df_pid.sample(n=5)
    repeat_catch_trials_rep1['catch_trial'] = "repeat"
    repeat_catch_trials_rep2 = repeat_catch_trials_rep1.copy()
    repeat_catch_trials_rep1['rep'] = 1
    repeat_catch_trials_rep2['rep'] = 2
    df_exp = pd.concat([df_exp, gt_catch_trials, repeat_catch_trials_rep1, repeat_catch_trials_rep2])
    
df_exp = df_exp.sample(frac=1).sort_values(by='pID', kind='mergesort')
print(df_exp)
print(len(df_exp[(df_exp['pID'] == 0)]))

105
       pID  experiment               stim1  \
6351     0           3   mi_5_ground_truth   
9723     0           2    905_ground_truth   
15720    0           3  mi_10_ground_truth   
14037    0           3   mi_2_ground_truth   
12451    0           2    291_ground_truth   
...    ...         ...                 ...   
1009   150           2    504_ground_truth   
7256   150           3   mi_4_ground_truth   
5268   150           1    656_ground_truth   
2946   150           3  mi_11_ground_truth   
5110   150           1    577_ground_truth   

                                     stim2  \
6351                  838_subject2_mindeye   
9723              246_subject5_secondsight   
15720        22_subject7_tagaki_low_random   
14037     58_subject7_braindiffuser_random   
12451              24_subject7_secondsight   
...                                    ...   
1009              171_subject1_secondsight   
7256                  466_subject2_mindeye   
5268                  656_sub

In [ ]:
version = 4
df_exp.to_csv(f'../experiments/dataframes/experiment_v{version}.csv', index=False)
df_exp_tsv = df_exp[['pID', 'stim1', 'stim2', 'stim3']].copy()
df_exp_tsv.to_csv(f"../experiments/dataframes/experiment_v{version}_meadow_trials.tsv", sep="\t", index=False, header=False) 

# THE FOLLOWING CELLS ARE FOR PROCESSING RESPONSES

In [141]:
response_path = "../experiments/responses/"
dataframe_path = "../experiments/dataframes/"
df_experiment = pd.read_csv(dataframe_path + "experiment_v4.csv")
response_version = 4
df_responses = pd.read_csv(f"{response_path}deployment_v{response_version}.csv")
# df_responses = df_responses[df_responses['participation'] == "poetic-mongoose"]

In [112]:
df_responses.head()
df_trial = pd.DataFrame(columns=["experiment", "stim1", "stim2", "stim3", "sample", "subject", "target_on_left", "iter_count", "is_low", "method", "catch_trial", "rep", "mode", "picked_left", "participant"])
df_experiment['picked_left'] = None
for index, row in tqdm(df_responses.iterrows()):
    if row['label'] == row['stim2_id']:
        picked_left = True
    elif row['label'] == row['stim3_id']:
        picked_left = False
    else:
        print("Error")
        break
    # df_experiment[(df_experiment['ground_truth'] == row['stim1_name']) & (df_experiment['stim1'] == row['stim2_name']) & (df_experiment['stim2'] == row['stim3_name'])]['picked_left'] = picked_left
    df_trial.loc[index] = df_experiment[(df_experiment['stim1'] == row['stim1_name']) & (df_experiment['stim2'] == row['stim2_name']) & (df_experiment['stim3'] == row['stim3_name'])].iloc[0]
    df_trial.loc[index, 'picked_left'] = picked_left
    df_trial.loc[index, 'participant'] = row['participation']
df_trial["picked_target"] = df_trial["picked_left"] == df_trial["target_on_left"]
print(df_trial)

0it [00:00, ?it/s]/tmp/ipykernel_24670/3834631837.py:13: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_trial.loc[index] = df_experiment[(df_experiment['stim1'] == row['stim1_name']) & (df_experiment['stim2'] == row['stim2_name']) & (df_experiment['stim3'] == row['stim3_name'])].iloc[0]
/tmp/ipykernel_24670/3834631837.py:13: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_trial.loc[index] = df_experiment[(df_experiment['stim1'] == row['stim1_name']) & (df_experiment['stim2'] == row['stim2_name']) & (df_experiment['stim3'] == row['stim3_name'])].iloc[0]
/tmp/ipykernel_24670/3834631837.py:13: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explici

      experiment              stim1                       stim2  \
0              2   170_ground_truth    170_subject2_secondsight   
1              2   470_ground_truth    393_subject2_secondsight   
2              3  mi_6_ground_truth        788_subject2_mindeye   
3              2   935_ground_truth    922_subject1_secondsight   
4              1   367_ground_truth        367_subject1_mindeye   
...          ...                ...                         ...   
13869          3  mi_0_ground_truth        623_subject7_mindeye   
13870          1   506_ground_truth        506_subject7_mindeye   
13871          3  mi_9_ground_truth  438_subject7_tagaki_random   
13872          1   499_ground_truth    499_subject5_secondsight   
13873          1   616_ground_truth    616_subject2_secondsight   

                                 stim3 sample subject target_on_left  \
0             263_subject2_secondsight    170       2           True   
1             470_subject2_secondsight    470      

In [137]:
# number of participants
print("Total participants:", len(df_trial["participant"].unique()))

# Remove participants who failed the ground truth catch trial, no tolerance
participants_to_remove_rule1 = df_trial[(df_trial['catch_trial'] == 'ground_truth') & (df_trial['picked_target'] == False)]['participant'].unique()

# Remove participants who failed the repeat catch trial, with a 3 strike allowance
repeat_offenses = df_trial[(df_trial['catch_trial'] == 'repeat') & (df_trial['picked_target'] == False)].groupby('participant').size()
participants_to_remove_rule2 = repeat_offenses[repeat_offenses >= 4].index.tolist()

participants_to_remove = set(participants_to_remove_rule1).union(set(participants_to_remove_rule2))
filtered_df = df_trial[~df_trial['participant'].isin(participants_to_remove)]
print("Clean participants:", len(filtered_df["participant"].unique()))
print(len(df_trial), len(filtered_df))
print(participants_to_remove)


Total participants: 116
Clean participants: 111
13874 13274
{'famous-monster', 'wondrous-caiman', 'natural-panda', 'frank-grubworm', 'exact-quetzal'}


In [153]:

df_trial_exp = filtered_df[filtered_df['catch_trial'].isnull()]
print(len(filtered_df), len(df_trial_exp))
df_trial_exp1 = df_trial_exp[(df_trial_exp['experiment'] == 3)]
# df_trial_exp1 = df_trial[(df_trial['experiment'] == 3) & (df_trial['mode'] == "vision")]
# df_trial_exp1 = df_trial[(df_trial['experiment'] == 3) & (df_trial['method'] == "secondsight") & (df_trial['mode'] == "vision") & (df_trial['is_low'] == False)]
print("Number of experiment trials", len(df_trial_exp1))
print(len(df_trial_exp1[df_trial_exp1["picked_target"]]) / len(df_trial_exp1))

13274 11620
Number of experiment trials 5884
0.7493201903467029


In [158]:
df_trial_exp.head(100)
for index, row in df_trial_exp[(df_trial_exp['experiment'] == 3)].iterrows():
    for stim in [row['stim2'], row['stim3']]:
        if "vision" in stim.split("_"):
            df_trial_exp.at[index, "mode"] = "vision"
        elif "imagery" in stim.split("_"):
            df_trial_exp.at[index, "mode"] = "imagery"
    sample_id = int(row['stim1'].split("_")[1])
    if sample_id <= 5:
        df_trial_exp.at[index, "stimtype"] = "simple"
    else:
        df_trial_exp.at[index, "stimtype"] = "complex"

df_trial_exp.to_csv(f'{dataframe_path}responses_v{response_version}_clean.csv', index=False)

/tmp/ipykernel_24670/1682097736.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_trial_exp.at[index, "stimtype"] = "complex"


5884
2976
2908
2975
2909
